모듈 불러오기

In [4]:
import os
import json
from transformers import AutoModelForCausalLM,AutoTokenizer
import torch
from torch.nn.utils.rnn import pad_sequence
from PyPDF2 import PdfReader
from sentence_transformers import SentenceTransformer
import faiss
import numpy as np
import nltk
nltk.download('punkt')
from transformers import BitsAndBytesConfig
import re

[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\wjkr0\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!


문서 ocr 후 저장

PDF 읽고 정제

In [22]:
import PyPDF2
from pykospacing import Spacing
import nltk
nltk.download('punkt')
from nltk.tokenize import sent_tokenize

# NLTK 다운로드
nltk.download('punkt')

# PDF 파일 경로
pdf_file_path = r'C:\lab_lm\pdf\2024 STARIA.pdf'
output_file_path = r'C:\lab_lm\extracted_text\final_extracted_text\STARIA_sentence.txt'

# PDF 파일 읽기
def read_pdf(file_path):
    with open(file_path, 'rb') as file:
        reader = PdfReader(file)
        text = ""
        for page in reader.pages:
            text += page.extract_text()
    return text

# 공백 제거 함수
def remove_spaces(text):
    return text.replace(" ", "").strip()

# PDF 파일 읽기
pdf_text = read_pdf(pdf_file_path)

# 공백 제거
cleaned_text = remove_spaces(pdf_text)

# PyKoSpacing을 사용하여 띄어쓰기 추가
spacing = Spacing()
corrected_text = spacing(cleaned_text)

# NLTK를 사용하여 문장 단위로 분할
sentences = sent_tokenize(corrected_text)

# 결과를 텍스트 파일로 저장
with open(output_file_path, 'w', encoding='utf-8') as file:
    for sentence in sentences:
        file.write(sentence + '\n')

print(f"Processed text has been saved to {output_file_path}")

[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\wjkr0\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\wjkr0\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!


문서 ocr 후 저장

In [1]:
#문서 단위 추출 후 임베딩 벡터 저장
def extract_text_from_pdfs(folder_path, output_folder, max_files=None):
    if not os.path.exists(output_folder):
        os.makedirs(output_folder)
    
    documents = []
    file_count = 0
    for filename in os.listdir(folder_path):
        if filename.endswith('.pdf'):
            filepath = os.path.join(folder_path, filename)
            with open(filepath, 'rb') as f:
                reader = PdfReader(f)
                text = ""
                for page in reader.pages:
                    text += page.extract_text()
                documents.append({'filename': filename, 'text': text})
                
                # 텍스트 파일로 저장
                base_filename = os.path.splitext(filename)[0]
                output_filepath = os.path.join(output_folder, base_filename + ".txt")
                with open(output_filepath, 'w', encoding='utf-8') as output_file:
                    output_file.write(text)
                
                file_count += 1
                if max_files and file_count >= max_files:
                    break
    return documents

folder_path = "C:\\lab_lm\\pdf"
output_folder = "C:\\lab_lm\\extracted_text"
documents = extract_text_from_pdfs(folder_path, output_folder, max_files=None)

# 결과 확인
print("Extracted documents:", documents)
print(f"Text files saved in {output_folder}")

NameError: name 'os' is not defined

In [ ]:
# 한국어 임베딩 모델 로드
embedder = SentenceTransformer('jhgan/ko-sroberta-multitask')

# 문서 로드 (이전 예제와 동일한 방법으로 documents 리스트를 생성)
data_path = "C:\lab_lm\extracted_text"

def load_documents(data_path):
    documents = []
    for filename in os.listdir(data_path):
        if filename.endswith('.txt'):
            filepath = os.path.join(data_path, filename)
            with open(filepath, 'r', encoding='utf-8') as file:
                text = file.read()
                documents.append(text)
    return documents

documents = load_documents(data_path)

# 문서 임베딩 계산
document_embeddings = embedder.encode(documents)

# FAISS 인덱스 생성 및 문서 임베딩 추가
index = faiss.IndexFlatL2(document_embeddings.shape[1])
index.add(np.array(document_embeddings))

# FAISS 인덱스 파일로 저장
index_file = "faiss_index.bin"
faiss.write_index(index, index_file)

print(f"FAISS index saved to {index_file}")

FAISS index saved to faiss_index.bin


문장 단위로 OCR 후 임베딩 벡터 저장

In [ ]:
# PDF에서 텍스트 추출 및 문장 단위로 분할하는 함수
def extract_text_from_pdfs(folder_path, output_folder, max_files=None):
    if not os.path.exists(output_folder):
        os.makedirs(output_folder)
    
    documents = []
    file_count = 0

    for filename in os.listdir(folder_path):
        if filename.endswith('.pdf'):
            filepath = os.path.join(folder_path, filename)
            with open(filepath, 'rb') as f:
                reader = PdfReader(f)
                text = ""
                for page in reader.pages:
                    page_text = page.extract_text()
                    if page_text:
                        text += page_text + "\n"
                
                # 텍스트 전처리
                text = text.replace("\n", " ").replace("\r", " ")
                text = ' '.join(text.split())

                # 문장 단위로 분할
                sentences = nltk.sent_tokenize(text)
                documents.append({'filename': filename, 'sentences': sentences})
                
                # 텍스트 파일로 저장
                base_filename = os.path.splitext(filename)[0]
                output_filepath = os.path.join(output_folder, base_filename + "_sentences.txt")
                with open(output_filepath, 'w', encoding='utf-8') as output_file:
                    for sentence in sentences:
                        output_file.write(sentence + "\n")
                
                file_count += 1
                if max_files and file_count >= max_files:
                    break

    return documents

folder_path = "C:\\lab_lm\\pdf"
output_folder = "C:\\lab_lm\\extracted_text"
documents = extract_text_from_pdfs(folder_path, output_folder, max_files=None)

# 결과 확인
print("Extracted documents:", documents)
print(f"Text files saved in {output_folder}")

Extracted documents: [{'filename': '2023 그랜저 하이브리드 GN7 HEV.pdf', 'sentences': ['안 전 및 차 량 손 상 경 고 본 취 급 설 명 서 에 는 고 객 및 차 량 의 안 전 을 위 해 유 의 해 야 할 사 항 과 제 품 사 용 에 대 한 정 확 한 정 보 를 알 리 는 안 전 경 고 표 시 가 포 함 되 어 있 습 니 다.', '지 시 사 항 을 반 드 시 숙 지 하 고 준 수 하 십 시 오.', '경 고, 주 의 표 시 경 고 , 주 의 가 있 는 문 장 및 진 하 게 표 시 되 어 있 는 부 분 은 특 히 유 념 하 십 시 오 .', '\x01҃\x01Ҋ 부 상 이 나 사 망 의 우 려 가 있 는 경 우 를 나 타 내 는 표 시 입 니 다 .', '\x01\u0ab1\x01\u0a44 차 량 이 고 장 나 거 나 손 상 될 우 려 가 있 는 경 우 를 나 타 내 는 표 시 입 니 다 .', 'iঌইفӝ 차 량 용 어 설 명 또 는 추 가 설 명 을 나 타 내 는 표 시 입 니 다 .', '안 전 을 위 해 반 드 시 지 켜 야 하 는 사 항 을 나 타 내 는 표 시 입 니 다 .', '선 택 또 는 미 장 착 사 양 표 시본 취 급 설 명 서 에 는 모 든 트 림 모 델 및 선 택 사 양 을 포 함 하 여 설 명 하 고 있 습 니 다 .', '고 객 님 의 차 량 에 장 착 되 지 않 는 사 양 에 대 한 설 명 이 포 함 될 수 있 습 니 다 .GN7_HEV_KO.book Page 1 내 용 찾 기 방 법 설 명 내 용 으 로 찾 을 때 목 차 를 활 용 하 세 요 .', '명 칭 을 모 를 때 그 림 목 차 (차 량 내 부 I) 를 활 용 하 세 요 명 칭 으 로 찾 을 때 색 인 (명 칭 ) 목 차 를 활 용 하 세 요 .', 'GN7_HEV_KO.book Page 2 제 작 결 함 안 내 자 동 차 제 작 자 등 (부 품 제 작 자 등 ): 현 대 자 동 차 (주 ) 주 소 : 서 울 특 별

In [8]:
# 한국어 임베딩 모델 로드
embedder = SentenceTransformer('jhgan/ko-sroberta-multitask')

def clean_filename(filename):
    # 파일 이름에서 특수 문자와 공백을 언더스코어로 대체
    return re.sub(r'[^a-zA-Z0-9_-]', '_', filename)

def embed_and_save_index(sentences, filename, output_folder):
    if not os.path.exists(output_folder):
        os.makedirs(output_folder)
    
    sentence_embeddings = embedder.encode(sentences)

    # FAISS 인덱스 생성 및 문장 임베딩 추가
    index = faiss.IndexFlatL2(sentence_embeddings.shape[1])
    index.add(np.array(sentence_embeddings))

    # 파일 이름 정리
    base_filename = clean_filename(os.path.splitext(filename)[0])

    # FAISS 인덱스 파일로 저장
    index_file = os.path.join(output_folder, base_filename + "_faiss_index.bin")
    faiss.write_index(index, index_file)

    # 문장 리스트 파일로 저장
    sentences_file = os.path.join(output_folder, base_filename + "_sentences.txt")
    with open(sentences_file, 'w', encoding='utf-8') as f:
        for sentence in sentences:
            f.write(sentence + "\n")

# 단일 텍스트 파일 로드 함수
def load_sentences(file_path):
    print(f"Loading sentences from: {file_path}")
    with open(file_path, 'r', encoding='utf-8') as file:
        sentences = file.read().splitlines()
    return sentences

file_path = r"C:\lab_lm\extracted_text\final_extracted_text\STARIA_sentence.txt"
output_folder = r"C:\lab_lm\faiss_indexes"
filename = os.path.basename(file_path)
sentences = load_sentences(file_path)

embed_and_save_index(sentences, filename, output_folder)

RAG + Ko-llama

In [8]:
# 한국어 임베딩 모델 로드
embedder = SentenceTransformer('jhgan/ko-sroberta-multitask')

# 모든 문서의 FAISS 인덱스를 로드하고 검색
def search_in_documents(query, data_path, top_k=2):
    query_embedding = embedder.encode([query])

    results = []
    for filename in os.listdir(data_path):
        if filename.endswith('_faiss_index.bin'):
            index_file = os.path.join(data_path, filename)
            index = faiss.read_index(index_file)
            
            sentences_file = index_file.replace('_faiss_index.bin', '_sentences.txt')
            with open(sentences_file, 'r', encoding='utf-8') as f:
                sentences = f.read().splitlines()

            # 검색
            distances, indices = index.search(np.array(query_embedding), top_k)

            # 인덱스 범위 유효성 검사 및 결과 추가
            for i in range(len(indices[0])):
                idx = indices[0][i]
                if idx < len(sentences):
                    result_sentence = sentences[idx]
                    results.append((result_sentence, distances[0][i], filename))
    
    # 거리 기준으로 정렬
    results = sorted(results, key=lambda x: x[1])
    return results[:top_k]

In [ ]:
# 질의 검색
query = "셉쿨러 하단 공기 누출 시 조치하는 법 알려줘"
data_path = "C:\\lab_lm\\faiss_indexes"
results = search_in_documents(query, data_path, top_k=1)

# 결과 출력
for result in results:
    print(f"Document: {result[2]}, Sentence: {result[0]}, Distance: {result[1]}")

In [4]:
# 모델과 토크나이저 로드 경로
model_path = "C:/lab_lm/model/5_qa_pair_trained_ko-llama3_model_3epochs"
tokenizer_path = r"C:\lab_lm\tokenizer\5_qa_pair_trained_ko-llama3_model_3epochs"

# 토크나이저 로드
tokenizer = AutoTokenizer.from_pretrained(tokenizer_path)
print("Tokenizer loaded successfully")

# 모델 로드
model = AutoModelForCausalLM.from_pretrained(model_path, torch_dtype=torch.bfloat16, device_map='cpu')
model.eval()
print("Model loaded successfully")

Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


Tokenizer loaded successfully


Loading checkpoint shards: 100%|██████████| 4/4 [00:01<00:00,  3.42it/s]
The installed version of bitsandbytes was compiled without GPU support. 8-bit optimizers, 8-bit multiplication, and GPU quantization are unavailable.


Model loaded successfully


In [5]:
import re

def generate_answer_with_rag(query, model, tokenizer, data_path, max_new_tokens=150, top_k=1):
    # 관련 문장 검색
    retrieved_sentences = [result[0] for result in search_in_documents(query, data_path, top_k=top_k)]
    print(retrieved_sentences)
    reference = "\n".join(retrieved_sentences)

    PROMPT = '''당신은 현대 자동차 메뉴얼에 관한 챗봇입니다. 사용자에게 친절하고 정확하게 답변해주시고 만약 검색된 외부지식이 포함될 경우 외부지식을 활용해서 답변해주세요.'''

    # 프롬프트 작성
    formatted_query = f"### 외부지식\n\n{reference}\n\n### 질의\n\n{query}"
    
    messages = [
        {'role': 'system', 'content': PROMPT},
        {'role': 'user', 'content': formatted_query}
    ]

    input_ids = tokenizer.apply_chat_template(
    messages,
    add_generation_prompt=True,
    return_tensors="pt"
    ).to(model.device)

    terminators = [
      tokenizer.eos_token_id,
      tokenizer.convert_tokens_to_ids("<|eot_id|>")
    ]

    # 모델을 사용하여 답변 생성
    outputs = model.generate(
        input_ids,
        max_new_tokens=max_new_tokens,
        do_sample=True,
        temperature=0.6,
        top_p=0.7,
        #repetition_penalty=1.5,
        #no_repeat_ngram_size=4,
        eos_token_id=terminators,  # eos_token_id를 pad_token_id로 설정
    )

    # 생성된 텍스트 디코딩
    answer = tokenizer.decode(outputs[0], skip_special_tokens=True)

    return answer

In [ ]:
# RAG 파이프라인 테스트
query = "셉쿨러 하단 공기 누출 시 조치하는 법 알려줘"
data_path = "C:\\lab_lm\\faiss_indexes"
answer = generate_answer_with_rag(query, model, tokenizer, data_path)
print("Answer:", answer)